## Unsuccessful. Only use the code for reference. For successful BERT training code, see AuxiliaryPrograms/TrainingBERT/loadtextclassificationmodel.ipynb

Semantic search using BERT and cosine similarities.

Author: Jerry Zou

In [14]:
from transformers import AutoTokenizer, AutoModel
import torch, os
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np

In [15]:
model = "bert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(model)
model = AutoModel.from_pretrained(model)

In [16]:
def embedding(text):
    input = tokenizer(text, return_tensors="pt", truncation=True, padding="max_length", max_length=256)
    output = model(**input)
    return output.last_hidden_state.mean(dim=1).detach().numpy()

In [17]:
folderPath = "/Users/Jerry/Desktop/Submission Diary entries"
fileNameContent = {}
for fileName in os.listdir(folderPath):
    if fileName.endswith(".txt"):
        fileTitle = os.path.join(folderPath, fileName)
        with open(fileTitle, "r", encoding="utf-8") as fileOpen:
            content = fileOpen.read()
            content = content.split(". ")
            fileNameContent[fileName] = content
#print(fileNameContent)

In [18]:
keywords = [
    "Who could check? No one had the resources or the desire to sift through hundreds of millions of turgid, overwritten pages on the voyant by a bunch of colourless drones",
    "With her broad shoulders, her grey crew cut and her courses in 'gender studies', Chantal Delouze, the president of Paris III, had always struck me as a dyed-in-the-wool lesbian",
    "nothing less than a political shift in the leadership of the French university system could ever rouse him",
    "It's true that Christianity and Islam have been at war for a very long time",
    "the only reason that the Socialists gave way on education or reached a deal with the Brotherhood - the only reason their pro-immigrant wing won out over the secularists - is that they were cornered"
]

# Change keywords list as fitting for each context of usage.

embedKeywords = [embedding(word) for word in keywords]

In [19]:
def contentEmbedding(text):
    sentenceEmbeddings = []
    for sentence in text:
        if sentence.strip():
            print(f"sentence: {sentence}")
            sentenceEmbeddings.append(embedding(sentence))
    return sentenceEmbeddings

def matchKeywords(texts, wordEmbeddings, threshold=0.8):
    matchComparison = {}
    for title, text in texts.items():
        print(title)
        sentenceEmbed = contentEmbedding(text)

        fittingSentence = None
        fittingSimilarityScore = 0
        for lineIndex, lineEmbedding in enumerate(sentenceEmbed):
            similarities = []
            print(f"line index: {lineIndex}")
            for value in wordEmbeddings:
                print(f"value: {value}")
                reshapedSentenceEmb = lineEmbedding.reshape(1, -1)
                reshapedWordEmbed = value.reshape(1, -1)
                similarityMatrix = cosine_similarity(reshapedSentenceEmb, reshapedWordEmbed)
                similarityValue = similarityMatrix[0][0]
                similarities.append(similarityValue)

            averageSimilarity = np.mean(similarities)
            if averageSimilarity > fittingSimilarityScore and averageSimilarity > threshold:
                fittingSimilarityScore = averageSimilarity
                fittingSentence = (text[lineIndex], averageSimilarity)
        if fittingSentence:
            if title not in matchComparison:
                matchComparison[title] = []
            matchComparison[title].append(fittingSentence)
    return matchComparison

keywordMatches = matchKeywords(fileNameContent, embedKeywords)

# Display results
for file, matches in keywordMatches.items():
    print(f"File: {file}")
    for line, similarity in matches:
        print(f"Line: {line}, Similarity: {similarity}")

Submission2.1.txt
sentence: ﻿After Myriam left, I kept to myself for more than a week
sentence: For the first time since I'd been made a professor, I didn't even feel up to teaching my Wednesday classes
sentence: The intellectual summits of my life had been completing my dissertation and publishing my book, and that was already more than ten years ago
sentence: Intellectual summits? Summits, full stop
sentence: In those days, at least, I'd felt justified
sentence: Since then I hadn't produced anything except a few short articles for the Journal of Nineteenth-Century Studies, plus a couple for The Literary Review, when some new book touched on my field of expertise
sentence: My articles were clear, incisive and brilliant
sentence: They were generally well received, especially since I never missed a deadline
sentence: But was that enough to justify a life? And why did a life need to be justified? Animals live without feeling the least need of justification, as do the crushing majority of